**[YOU CAN VIEW THIS NOTEBOOK INCLUDING THE INTERACTIVE PLOTS USING THIS LINK](https://nbviewer.jupyter.org/github/DCMLab/schubert_dances/blob/master/schubert_project.ipynb?flush_cache=true)**

<font size=15>Table of Contents</font>
- [about this project](#about-this-project)
  * [abstract](#abstract)
  * [research questions and hypotheses](#research-questions-and-hypotheses)
  * [dataset](#dataset)
- [configuration](#configuration)
- [helper functions](#helper-functions)
- [loading the data](#loading-the-data)
  * [computing or loading the dataframe representation of the music](#computing-or-loading-the-dataframe-representation-of-the-music)
- [basic statistics](#basic-statistics)
  * [pieces per dance type](#pieces-per-dance-type)
  * [constellations of sections](#constellations-of-sections)
  * [section lengths](#section-lengths)
  * [distribution of key signatures](#distribution-of-key-signatures)
  * [number and distribution of notes](#number-and-distribution-of-notes)
    + [average note duration](#average-note-duration)
  * [distribution of transposed notes](#distribution-of-transposed-notes)
  * [time signatures](#time-signatures)
  * [entropy of the pitch class distribution](#entropy-of-the-pitch-class-distribution)
  * [provisional mode classification](#provisional-mode-classification)
    + [key profiles](#key-profiles)
  * [event density](#event-density)
  * [interval statistics for top pseudo-voice](#interval-statistics-for-top-pseudo-voice)
    + [distribution by dance type](#distribution-by-dance-type)
- [roadmap for the project](#roadmap-for-the-project)
  * [repeating pattern detection with autocorrelation](#repeating-pattern-detection-with-autocorrelation)
  * [harmony inference and detection of musical schemata](#harmony-inference-and-detection-of-musical-schemata)
  * [supervised classification of dance types](#supervised-classification-of-dance-types)
- [Internal: How plotting works](#internal--how-plotting-works)

<small><i><a href='http://ecotrust-canada.github.io/markdown-toc/'>Table of contents generated with markdown-toc</a></i></small>



# about this project
## abstract
>Everybody has an emotional access to music, which in turn transports listeners into specific moods, atmospheres and settings. This intuitive understanding of musical pieces is grounded in structural elements such as melodic motives and rhythms, with their variations or repetitions.<p> 
Our project aims at gaining an objective insight into how these patterns engender different shades of musical engagement. Specifically, we will investigate the structure and composition of Franz Schubert's "dances", a large set of 400 piano pieces classified in seven different types according to their times’ conventions. The conventionality of these short and catchy pieces makes them an ideal testing ground for computer-assisted analysis, but also makes them highly representative of the taste of early-nineteenth-century listeners. With our statistical investigation we hope to open a window onto this past: what did listeners expect of appealing dance-like music, and did different dance types correspond to different musical features or just to different social perspectives on the same musical features?

**Update** After the first analysis of our data set we are confident that we have the means to give a tentative answer to the question whether the different dance types display essential differences in their musical features or whether the difference lies mainly in their denomination. In the section [Key signatures](#key-signatures) we show that all dances are either in double (2/4) or triple meter (3/4) which are, of course, musically distinct on first hearing. Therefore the aforementioned question diversifies into classification between dance types in double meter and between those in triple meter respectively. Also, we now have eight instead of seven different dance types because we decided to evaluate *Trio* sections as separate types for two reasons. On the one hand, it can be expected that Trios differ in their musical parameters. On the other hand, they often introduce new motives, rhythms and key signatures and therefore can be considered as separate pieces.
    
## research questions and hypotheses

>1. What recurring patterns and regularities make Schubert's dances so intuitively appealing and easy to grasp? Possible levels of investigation:
  * rhythmic patterns
  * melodic patterns
  * harmonic makeup
  * formal level
2. Are the different dance types musically distinguishable? Which features will a classifier use to distinguish the different dance types? Hypothetically, these features will include:
  * meter
  * melodic motives and shapes
  * musical form
  * harmonic progressions
  * rhythmic markup
  * musical texture
  * relation between the two hands

**Update** The research questions have stayed unchanged. When discussing each team member's contribution it turned out that Sébastien and Johannes H. will deal with aspects of question 1. Their contributions (see [Roadmap for the project](#roadmap-for-the-project)) will result in new features, namely segmentations with similarity scores, chord labels, and instances of musical sequences (i.e., transposed repetitions of a segment). Gabriele and Johannes R. will be involved with question 2 and can potentially involve features newly computed by SR & JH for the classification task.
    
## dataset
>The dataset consists of the scores, in MuseScore 3 XML format, of all 394 dances written for piano by Franz Schubert (1797-1828). [...]

**Update** Naturally, the data set is very apt for answering our questions because our questions are based on this data set. By separating the Trios into their own files, we are now dealing with 435 scores. Also, we have excluded the 6 dances which are doublings of other ones and matched the filenames to the IDs that the music theorist Yosef Goldenberg of the Jerusalem Academy of Music and Dance uses in his manual analysis of the data set. This way, we might use his analyses as ground truth data if the opportunity presents itself.

In the section [Basic statistics](#basic-statistics) we prove that the parser is working and that the representation it yields serves our goals. Each piece is represented by one dataframe per section (sections have been inferred from repetition signs and double bar lines). Each dataframe contains the list of notes for the respective section with each note's features. The point of departure for all our analyses is the concatenated note list of all sections of all pieces which we have stored [as a TSV file](https://raw.githubusercontent.com/DCMLab/schubert_dances/master/data/tsv/note_list_complete.tsv). Additionally, we make use of the [file measure_list_complete.tsv](https://raw.githubusercontent.com/DCMLab/schubert_dances/master/data/tsv/measure_list_complete.tsv) which contains high level information about every bar (note that the words bar and measure can be used interchangeably), such as meter, key signature or measure number.
>Note that MuseScore XML files contain one \<Measure\> node for every bar line and that we address these units with running numbers starting at zero which we call **measure counts (mc)**. The **measure numbers (mn)**, however, are those that are displayed/printed in the score. Measure numbers frequently span multiple measure counts and had to be computed by the parser following the usual conventions.

The representation as a note list is fortunate because it presents a musical piece in the form of numerical features while offering all the advantages of working with Python's `pandas` package. Here, we briefly explain the features that have been extracted from the scores for every note:
    
**Index**
* **id**: one ID per piece for easy addressing
* **section**: in which section of the piece a note appears
* **ix**: running number of notes in this section
    
**Columns**
* **mc**: measure count (see box above)
* **mn**: measure number
* **onset**: temporal position of the note relative to the previous bar line expressed in quarter beats (see explanation for `duration` below)
* **duration**: duration of the note expressed in quarter beats; a quarter beat has the length of 1/4 of a whole note (or a 4/4 measure); therefore a half note (or a 2/4 measure) has length 2 and a dotted half note (or a 3/4 measure) has length 3)
* **gracenote**: whether or not the note is a grace note and which type; grace notes are ornamental and likely to be excluded from most automated analyses; this is the only non-numerical feature but will be mainly used as a boolean value such that `Nan = False`, i.e. 'not a grace note'.
* **nominal_duration**: note value before applying the altering `scalar`
* **scalar**: value encoding the alteration of the `nominal_duration` caused by dots and triplets (or other n-tuples)
* **tied**: three possible values (other than NaN):
  * `1` if the note is tied to the next one (meaning that the next one is not causing a new attack)
  * `-1` if the note is being tied to by the previous note (meaning that it prolongs the previous note's duration)
  * `0` if the note is being tied to AND is tied to the next one (i.e. `-1 + 1 = 0`)
* **tpc**: stands for Tonal Pitch Class and is a numerical encoding of tone names such that `C = 0`. All other names are ordered along the line of fifths:
  * descending from C: `F = -1`, `Bb = -2`, `Eb = -3` etc.
  * ascending from C: `G = 1`, `D = 2`, `A = 3` etc.
* **midi**: encodes which piano key needs to be pressed to produce this note, meaning that `midi` information encodes in which octave the note is sounding (unlike `tpc`) but not as which note name the note is written in the score (note that the same key on the piano is pressed to produce different note names (`tpc`s), for example the key `midi == 66` can be written in a score as F#4 (`tpc == 6`) , Gb4 (`tpc == -6`), E##4 (`tpc == 17`), Abbb4 (`tpc == -18`) etc. where 4 designates octave 4).
* **staff**: whether a note is written in the right hand (`staff == 1`) or in the left hand (`staff == 2`)
* **voice**: In Common Music Notation, when simultaneously sounding notes with different durations appear in the same `staff`, they have to be written in different layers. MuseScore can represent up to four different layers per `staff`, with `voice == 1` usually represents the highest. Note that this is the notational notion of the word 'voices', not the musical one: `voice == 1` can contain more than one simultaneous event with the same `onset` and `duration` (i.e., a chord), whereas in the musical sense, an 'upper voice' or 'melody' consists only of one note at a time and is difficult to automatically extract from a score.
* **volta**: Some repeated sections are played with different endings the first (`volta == 1`) and the second time (`volta == 2`). These endings ('voltas') can span one or multiple measures and the measures in a second volta have the same measure numbers as the ones in the first.
    
For every measure count, notes are ordered first horizontally (by `onset`), then vertically (by `midi`).

In [192]:
%load_ext autoreload
%autoreload 2
# import os
# os.chdir(/path/to/git_folder)
from tools.ms3 import *
import itertools
import scipy as sp
from plotly.offline import iplot
import plotly.express as px
import cufflinks as cf # for creating plots from pandas on the fly
import plotly.io as IO
cf.go_offline()
cf.set_config_file(theme='ggplot') #{'solar', 'pearl', 'white', 'ggplot'}

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


# configuration 

In [193]:
compute_all = False                              # Sets all 'compute_anew' flags to True
logging.getLogger().setLevel(logging.WARNING)    # logging level
data ='data'                                     # data folders
data_ms3 = os.path.join(data,'MuseScore_3')
data_tsv = os.path.join(data,'tsv')
note_features = None                             # TODO: Pass selected features as kwargs to get_notes()
#plt.rcParams['figure.figsize'] = [15,10]        # Change the plotsize for matplotlib in the entire notebook
std_plotsize = (1100, 500)                       # Standard plotsize (in px) for storing plotly images to disk 
                                                 # (the ones in the notebook adapt to windows size)

# helper functions

In [194]:
def plot(df, fname='test.png', kind='scatter', size=std_plotsize,  **kwargs):
    """Used to store plots as graphics."""
    fig = df.iplot(asFigure=True,kind=kind, **kwargs)
    #fig.update(layout={})
    w, h = size[0], size[1]
    IO.write_image(fig, fname, width=w, height=h)
    iplot(fig)

In [195]:
def bag_of_notes(df, tpc='tpc'):
    """Input: DataFrame including the columns ['tpc', 'duration'].
    Output: Note distribution."""
    tpcs = df.tpc
    occurring = np.sort(tpcs.unique())
    bag = pd.DataFrame(index=occurring, columns=['count_a', 'count_n', 'duration_a', 'duration_n'])
    GB = df.groupby('tpc')
    bag.count_a = GB.size()
    bag.count_n = bag.count_a / bag.count_a.sum()
    bag.duration_a = GB['duration'].sum().astype(float)
    bag.duration_n = (bag.duration_a / bag.duration_a.sum()).astype(float)
    if tpc != 'tpc':
        names = tpc.split('+')
        note_names = []
        for n in names:
            if n == 'tpc':
                note_names.append(occurring)
            elif n == 'name':
                note_names.append(tpc2name(occurring))
            elif n == 'degree':
                note_names.append(tpc2degree(occurring))
            elif n == 'pc':
                note_names.append(tpc2pc(occurring))
            else:
                logging.warning("Parameter tpc can only be {'tpc', 'name', 'degree', 'pc'} or a combination such as 'tpc+pc' or 'name+degree+tpc'.")
        L = len(note_names)
        if L == 0:
            note_names.append(bag.index)
            L = 1
        if L == 1:
            bag.index = note_names[0]
        else:
            bag.index = [f"{t[0]} ({', '.join(str(e) for e in t[1:])})" for t in zip(*note_names)]
    return bag

# loading the data
The dataframe `merged_ids` maps the 435 IDs to the files in the `data_ms3` folder. The different types of trios (trio I, trio II, alternative trio) are all replaced by the term 'trio'.

In [196]:
merged_ids = os.path.join(data_ms3, 'merged_ids.tsv')
files = pd.read_csv(merged_ids, sep='\t', index_col=0)
files.loc[files.dance.str.contains('trio'), 'dance'] = 'trio'
files.head()

D  no    dance                     path
id                                          
1   41   1  menuett  041/D041menuett01a.mscx
2   41   1     trio     041/D041trio01b.mscx
3   41   2  menuett  041/D041menuett02a.mscx
4   41   2     trio     041/D041trio02b.mscx
5   41   3  menuett  041/D041menuett03a.mscx

**Accessibility**
We check whether all files are accessible.

In [197]:
missing = [file for file in files.path.values if not os.path.isfile(os.path.join(data_ms3, file))]
if missing != []:
    print("These files are missing:\n" + '\n'.join(missing))
else:
    print("All files found.")

All files found.


## computing or loading the dataframe representation of the music
We will be working on the data set in the form of note_lists. These can be newly computed from the scores or loaded from the precomputed TSV.

In [198]:
compute_anew = False

if compute_anew or compute_all:

    parse_score = lambda path: Score(os.path.join(data_ms3,path))
    score_objects = pd.DataFrame(files.path.apply(parse_score)).rename(columns={'path': 'object'})
    note_list = score_objects.groupby('id').apply(lambda df: df.iloc[0,0].get_notes(volta_warning=False))
    note_list.to_csv(os.path.join(data_tsv, 'note_list_complete.tsv'), sep='\t')
    measure_list = score_objects.groupby('id').apply(lambda df: df.iloc[0,0].info)\
                                .astype({'section': int, 
                                         'keysig': int, 
                                         'voices': int, 
                                         'volta': 'Int64', 
                                         'numbering_offset': 'Int64', 
                                         'dont_count': 'Int64'})
    measure_list.to_csv(os.path.join(data_tsv, 'measure_list_complete.tsv'), sep='\t')
    section_order = score_objects.applymap(lambda x: x.section_order).rename(columns = {'path': 'sections'})
    section_order.to_csv(os.path.join(data_tsv, 'section_order_complete.tsv'), sep='\t')
    
else:
    note_list = pd.read_csv(os.path.join(data_tsv, 'note_list_complete.tsv'), sep='\t', index_col=[0,1,2], 
                            dtype={'tied': 'Int64', 
                                   'volta': 'Int64'}, 
                            converters={'onset':frac, 
                                        'duration':frac, 
                                        'nominal_duration':frac, 
                                        'scalar':frac})
    measure_list = pd.read_csv(os.path.join(data_tsv, 'measure_list_complete.tsv'), sep='\t', index_col=[0,1], 
                               dtype={'volta': 'Int64', 
                                      'numbering_offset': 'Int64', 
                                      'dont_count': 'Int64'}, 
                               converters={'timesig': frac, 
                                           'duration': frac, 
                                           'act_dur': frac, 
                                           'offset': frac, 
                                           'next': lambda l: [int(mc) for mc in l.strip('[]').split(', ') if mc != '']})
    section_order = pd.read_csv(os.path.join(data_tsv, 'section_order_complete.tsv'), sep='\t', index_col = [0])\
                      .rename(columns={'object': 'sections'})
## converters={'object': lambda l: [int(s) for s in l.strip('[]').split(', ')]}
                                
    note_list.head()

## loading ground truth data

### major vs minor ground truth


In [199]:
GT_ma_mi = pd.read_csv(os.path.join(data_tsv, 'GT_ma_mi.tsv'), sep='\t', index_col=[0])['mode']
GT_ma_mi.value_counts()

major    372
minor     63
Name: mode, dtype: int64

In [200]:
files['gt_mode'] = GT_ma_mi

# basic statistics

## pieces per dance type

In [201]:
dance_types = files.dance.value_counts()
print(f"The corpus contains {len(files.index)} pieces. The different types are distributed as follows:{NL}{dance_types}")
dance_types.iplot('bar')

The corpus contains 435 pieces. The different types are distributed as follows:
walzer       132
ländler       78
ecossaise     74
deutscher     71
trio          48
menuett       29
galopp         2
cotillon       1
Name: dance, dtype: int64


## constellations of sections

In [202]:
print('The vast majority of the dances is notated in two repeated sections, AABB.')
section_order.sections.value_counts().iplot('bar')

The vast majority of the dances is notated in two repeated sections, AABB.


## section lengths

In [203]:
print('Most sections are normatively 8 measures long (measure-count 8 or 9 depending on repetition), but there are also several 16 measure-long sections: it could be hypothesised that these sections are internally binary.')
measure_list.groupby(['id', 'section']).size().value_counts().iplot('bar', xTitle='Section length (in bars)', yTitle='Count')

Most sections are normatively 8 measures long (measure-count 8 or 9 depending on repetition), but there are also several 16 measure-long sections: it could be hypothesised that these sections are internally binary.


## distribution of key signatures

In [204]:
measure_list.keysig.sort_values().apply(tpc2key).iplot('hist', xTitle='Key', yTitle = 'Fraction of bars with given key signature', histnorm = 'probability')

## number and distribution of notes

In [205]:
print(f"The data set has {len(note_list.index)} note events in total, and {len(note_list.index[note_list.gracenote.isna()])} notes without grace notes.")

The data set has 101810 note events in total, and 101231 notes without grace notes.


In [206]:
tpc_distribution = bag_of_notes(note_list, 'name')

In [207]:
tpc_distribution[['count_a', 'duration_a']].iplot('bar', xTitle='Tonal Pitch Class', yTitle='Absolute note counts<br>Durations (in quarter beats)')

In [208]:
tpc_distribution[['count_n', 'duration_n']].iplot('bar', xTitle='Tonal Pitch Class', yTitle='Normalized note counts & durations')

### average note duration

The duration and count of tonal pitch-classes are analogously distributed over the corpus. This implies that the average duration of each note is roughly independent of its tonal pitch class.

In [209]:
average_duration = pd.DataFrame(tpc_distribution['duration_a']/tpc_distribution['count_a'], columns = ['Average duration'])

average_duration.iplot('bar')

The common average duration is close to a quarter note, which is also the common tactus of all the dances (that are only written in 3/4 or 2/4 meter).

## distribution of transposed notes
All pitches are transposed to C major / a minor by substracting the key signature from `tpc`

*Example*: `keysig == 1` &rightarrow; 1 sharp &rightarrow; key of G major (or E minor) &rightarrow; tonic = G = `tpc == 1` &rightarrow; transposition to C major (or A minor) by subtracting 1

In [210]:
note_list_transposed = note_list.merge(measure_list['keysig'], on=['id', 'mc'], right_index=True)   # Add a column with the corresponding key signature for every note
note_list_transposed.tpc -= note_list_transposed.keysig                                             # subtract key signature from tonal pitch class (=transposition to C)
midi_transposition = tpc2pc(note_list_transposed.keysig)\
                     .apply(lambda x: x if x <= 6 else x % -12)                                     # convert key signature to pitch class and decide whether MIDIs are shifted downwards (if <= 6) or upwards
up_or_down = (midi_transposition == 6)                                                              # if the shift is 6, the direction of shift depends on the key signature:
midi_transposition.loc[up_or_down] = note_list_transposed[up_or_down].keysig\
                                     .apply(lambda x: 6 if x > 0 else -6)                           # If the key signature is F#, shift downwards, if it's Gb, shift upwards
note_list_transposed.midi -= midi_transposition                                                     # transpose MIDIs
transposed_distribution = bag_of_notes(note_list_transposed, 'degree+name')

In [211]:
transposed_distribution[['count_a', 'duration_a']].iplot('bar', xTitle='Scale degree (Note name)', yTitle='Absolute note counts<br>Durations (in quarter beats)')

In [212]:
transposed_distribution[['count_n', 'duration_n']].iplot('bar', xTitle='Scale degree (Note name)', yTitle='Normalized note counts & durations')

**Comment** After shifting all major pieces to C and all minor pieces to A, the distribution reveals two things:
* As is typical for music where most of the chords are rooted on `I` (*tonic* chords) or on `V` (*dominant* chords), the note of the `V`th degree is even more frequent than the root of the key (`I`) because the note `V` appears in the chord on `I` **and** in the chord on `V`.
* Apparently, the majority of the dances stands in major keys because otherwise we would expect higher ratios for `VI` (the minor root) and `#V` (its leading tone).
* A bimodal distribution can still be recognised, with a peak centered on the dominant of major keys and another one on the dominant of minor keys (`III`). However, the occurrence of the scale degree `III` is boosted by being a relevant component of both the major (mediant) and minor (dominant) relative keys. 

## time signatures

In [213]:
float_timesig = measure_list
float_timesig['timesig'] = measure_list.timesig.apply(str)
float_timesig.groupby('timesig').apply(lambda x: len(x)/len(measure_list)).iplot('bar', xTitle = 'Time signature', yTitle = 'Frequency')

## entropy of the pitch class distribution

For each dance, we compute the entropy of the distribution of tonal pitch classes, normalised to the alphabet of all 35 tpcs up to 2 accidentals.

In [214]:
note_list_by_dance = note_list.groupby('id').apply(lambda x: bag_of_notes(x, 'tpc'))
entropies = note_list_by_dance.groupby('id').apply(lambda x: sp.stats.entropy(x.count_a)/np.log(35))

entropies.iplot('hist', bins = 50, xTitle = 'Normalised entropy')



The entropy distribution seems to be independent of the key signature, with no significant (at 95% confidence and, if any, small in effect size) correlation between entropy and key signature or number of accidentals.

In [215]:
accidentals = note_list.merge(measure_list['keysig'], on=['id', 'mc'], right_index=True).groupby('id').keysig.max()
pd.DataFrame({'entropy': entropies, 'accidentals':  accidentals}).boxplot(column = 'entropy', by = 'accidentals');


#iplot('scatter', mode='markers', x = 'key_sig', y = 'entropy')

In [216]:
sp.stats.pearsonr(entropies, accidentals)

(0.08952387207358559, 0.06210530116047899)

In [217]:
sp.stats.pearsonr(entropies, accidentals.apply(abs))

(-0.05026059580713712, 0.2956013291762431)

### Entropy of pitch distribution

In [218]:
files['entropy'] = entropies

In [219]:
files.set_index('dance', append=True)\
     .entropy\
     .unstack(level=1)\
     .iplot('box', yTitle = 'entropy' )

### Entropy of durations distribution

In [220]:
files['duration_entropy'] = note_list.groupby('id').duration.value_counts().groupby('id').apply(lambda x: sp.stats.entropy(x))

files.set_index('dance', append=True)\
     .duration_entropy\
     .unstack(level=1)\
     .iplot('box', yTitle = 'durations entropy' )

### Entropy of onsets distributions

In [221]:
files['onset_entropy'] = note_list.groupby('id').onset.value_counts().groupby('id').apply(lambda x: sp.stats.entropy(x))

files.set_index('dance', append=True)\
     .onset_entropy\
     .unstack(level=1)\
     .iplot('box', yTitle = 'onset entropy' )

## provisional mode classification

The historically influential Krumhansl & Kessler (1982) key profiles classify pitch classes according to their perceived fit into a major or minor tonal context. The correlation of the pitch-class distribution of each dance with a key profile provides a first estimate of the fit of that dance into a mode (cf. Krumhansl, 1990). It should be noted that these key profiles are based on behavioural responses of listeners rather than on corpus statistics. 

In [222]:
def KK(mode, transposition):
    """Krumhansl and Kessler (1982) key profiles for major and minor modes"""
    
    major = [6.20, 2.55, 3.45, 2.85, 4.22, 4.57, 2.67, 5.25, 2.45, 3.35, 2.70, 2.70]
    minor = [6.03, 3.35, 3.67, 5.28, 2.58, 3.55, 2.87, 4.80, 4.35, 2.67, 2.50, 3.42]
    
    major_by_fifths = [None] * len(major)
    minor_by_fifths = [None] * len(minor)
    
    #reorder by fifths
    for i in range(len(major)):
        major_by_fifths[(i*7)%12] = major[i]
        minor_by_fifths[((i*7)+3)%12] = minor[i]
    
    #major = list(map(lambda x: x/sum(major), major))
    #minor = list(map(lambda x: x/sum(minor), minor))
    
    if mode == 0:   
        return major_by_fifths[-transposition:]+major[:-transposition]
    elif mode == 1:
        return minor_by_fifths[-transposition:]+minor[:-transposition]
    else:
        print('0 = major, 1 = minor')

### key profiles

In [223]:
pc_list = note_list_transposed
pc_list.tpc = pc_list.tpc.apply(lambda x: x%12)
pc_list_distr = pc_list.groupby('id').apply(lambda x: bag_of_notes(x, 'tpc'))

def full_distr(bag, index):
    key_profile_index = pd.MultiIndex.from_product([index, list(range(12))])
    key_profile = pd.DataFrame(index = key_profile_index, columns = ['profile']).fillna(0)

    for i in bag.index:
        key_profile.loc[i] = bag.loc[i].duration_n
    return key_profile

In [224]:
glob_key_profile = full_distr(pc_list_distr, files.index)
major_corr = pd.DataFrame(glob_key_profile.groupby(axis = 0, level = 0).profile.apply(lambda x: sp.stats.pearsonr(x, KK(0,0))[0])).rename(columns = {'profile': 'major'})
minor_corr = pd.DataFrame(glob_key_profile.groupby(axis = 0, level = 0).profile.apply(lambda x: sp.stats.pearsonr(x, KK(1,0))[0])).rename(columns = {'profile': 'minor'})
key_corr = pd.concat([major_corr, minor_corr], axis = 1)

In [225]:
major_dances_prov = files.loc[key_corr[key_corr.minor<=key_corr.major].index]
minor_dances_prov = files.loc[key_corr[key_corr.minor>key_corr.major].index]

print(f'According to this preliminary classification, there are {len(major_dances_prov)} dances whose global pitch-class distribution matches the major key profile better than the minor one, and {len(minor_dances_prov)} whose global pitch-class distribution matches the minor key profile better than the major one. ')

According to this preliminary classification, there are 401 dances whose global pitch-class distribution matches the major key profile better than the minor one, and 34 whose global pitch-class distribution matches the minor key profile better than the major one. 


In [226]:
minor_dances_prov.groupby('dance').size().iplot('bar', title = 'Distribution of minor mode dances (provisional)')

In [227]:
dances_mode = pd.DataFrame(files.groupby('dance').gt_mode.value_counts())
dances_mode.rename(columns = {'gt_mode': 'count'}, inplace = True)
dances_mode.reset_index(inplace = True)


In [228]:
px.bar(dances_mode, x = 'dance', y = 'count', color = 'gt_mode')

### mode recognition based on first section alone

In [229]:
pc_list_distr_A = pc_list[pc_list.index.get_level_values('section') == 0].groupby('id').apply(lambda x: bag_of_notes(x, 'tpc'))

In [230]:
A_key_profile = full_distr(pc_list_distr_A, files.index)
major_corr_A = pd.DataFrame(A_key_profile.groupby(axis = 0, level = 0).profile.apply(lambda x: sp.stats.pearsonr(x, KK(0,0))[0])).rename(columns = {'profile': 'major'})
minor_corr_A = pd.DataFrame(A_key_profile.groupby(axis = 0, level = 0).profile.apply(lambda x: sp.stats.pearsonr(x, KK(1,0))[0])).rename(columns = {'profile': 'minor'})
key_corr_A = pd.concat([major_corr_A, minor_corr_A], axis = 1)


In [231]:
major_dances_A = files.loc[key_corr_A[key_corr_A.minor<=key_corr_A.major].index]
minor_dances_A = files.loc[key_corr_A[key_corr_A.minor>key_corr_A.major].index]

print(f'When looking at the pitch distribution of first sections only, there are {len(minor_dances_A)} dances whose pitch profile is closer to the minor KK key profile than to the major one.')

When looking at the pitch distribution of first sections only, there are 55 dances whose pitch profile is closer to the minor KK key profile than to the major one.


In [232]:
GT_minor = pd.DataFrame(GT_ma_mi)
GT_minor = GT_minor[GT_minor['mode']=='minor'].index

detected_minor_A = minor_dances_A[minor_dances_A.index.isin(GT_minor)]
falsely_detected_minor_A = minor_dances_A[~minor_dances_A.index.isin(detected_minor_A.index)]
not_detected_minor_A = major_dances_A[major_dances_A.index.isin(GT_minor)]

print(f'This simple model successfully recognises {len(detected_minor_A)} of the {len(GT_minor)} dances labeled as minor in our ground-truth. It wrongly labels {len(falsely_detected_minor_A)} dances as minor and fails to recognise {len(not_detected_minor_A)} minor dances.')

This simple model successfully recognises 51 of the 63 dances labeled as minor in our ground-truth. It wrongly labels 4 dances as minor and fails to recognise 12 minor dances.


#### distribution of false positives/negatives by dance type

In [233]:
falsely_detected_minor_A.merge(key_corr_A, left_index = True, right_index = True)

D  no      dance                      path gt_mode   entropy  \
338  783   1  deutscher  783/D783deutscher01.mscx   major  0.624948   
346  783   9  deutscher  783/D783deutscher09.mscx   major  0.560845   
369  816   3  ecossaise  816/D816ecossaise03.mscx   major  0.582274   
415  972   2  deutscher  972/D972deutscher02.mscx   major  0.523915   

     duration_entropy  onset_entropy     major     minor  
338          0.750338       1.274454  0.475333  0.744253  
346          0.808492       1.391723  0.092300  0.165038  
369          0.868209       0.913351  0.677665  0.744747  
415          0.693094       1.611656  0.092300  0.165038

- D783.1 shifts immediately to relative minor. 
- D783.9 is parsed so that section 0 is only the pick-up measure. 
- D816.3 shifts to relative minor after first phrase.
- D972.2 is parsed so that section 0 is only the pick-up measure.

Dances with ID = 60, 103, 196, 223, 267, 275, 307, 346, 349, 375, 394, 413, 415 have the pick-up section issue.

In [234]:
not_detected_minor_A.merge(key_corr_A, left_index = True, right_index = True)

D  no      dance                      path gt_mode   entropy  \
56   128  10  deutscher  128/D128deutscher10.mscx   minor  0.562569   
63   145   3     walzer     145/D145walzer03.mscx   minor  0.614695   
69   145   9     walzer     145/D145walzer09.mscx   minor  0.592727   
194  366   9    ländler    366/D366ländler09.mscx   minor  0.604576   
198  366  13    ländler    366/D366ländler13.mscx   minor  0.598615   
314  779  23     walzer     779/D779walzer23.mscx   minor  0.575870   
342  783   5  deutscher  783/D783deutscher05.mscx   minor  0.540814   
348  783  11  deutscher  783/D783deutscher11.mscx   minor  0.548716   
351  783  14  deutscher  783/D783deutscher14.mscx   minor  0.633543   
355  783   2  ecossaise  783/D783ecossaise02.mscx   minor  0.555444   
389  924  11     walzer     924/D924walzer11.mscx   minor  0.554017   
397  969   5     walzer     969/D969walzer05.mscx   minor  0.619754   

     duration_entropy  onset_entropy     major     minor  
56           1.307103       1.588871  0.577539  0.222567  
63           0.716351       1.366746  0.718390  0.605821  
69           1.226204       1.410805  0.848188  0.598276  
194          0.923784       1.417350  0.756567 -0.022396  
198          0.833152       1.460061  0.663618  0.315752  
314          0.819098       1.590646  0.713975  0.375713  
342          0.982174       1.643418  0.868694  0.299102  
348          0.857530       1.624273  0.706857  0.651459  
351          0.830951       1.493292  0.718854  0.709965  
355          0.978762       1.007479  0.835016  0.165022  
389          0.781686       1.310137  0.923445  0.519277  
397          0.738836       1.460179  0.757260  0.544627

- D128.10 starts ambiguously, but F#min, but then Dmaj. I'd say it is Dmaj. 
- D145.3 starts Amin-->Cmaj, then Amaj
- D145.9 is F#min. Shift to the dominant might be confusing for the model.
- D366.9 I would say this is definitely Bmaj, although it starts in Bmin. The key signature is Bmaj (hence neg. corr with minor).
- D366.13 is Bbmin. Shift to relative major might be confusing for the model.
- D779.23 BEAUTIFUL! is Ebmaj, but starts with II/Gmin, and then moves to Eb through a deceptive cadence.
- D783.5 BEAUTIFUL! is Dmaj but starts with Bmin (just colouring).
- D783.11 starts Emin, then goes Gmaj till the end (correlation very close).
- D783.14 starts Fmin, then Abmaj, then second part in Fmaj (corr. very close).
- D783.2(ecossaise) starts Bmin (omophonic) but abruptly moves to Dmaj
- D924.11 starts in Emin, but just colouring. No cadence.
- D969.5 model is wrong. Strong Amin/Emin in the beginning.

It seems that deutscher and walzers are more likely to exhibit modal shifts in the beginning.

#### mode recognition based on first phrase

In [235]:
pc_list_distr_first = pc_list[(pc_list.index.get_level_values('section') == 0) & (pc_list.mc <= 4)].groupby('id').apply(lambda x: bag_of_notes(x, 'tpc'))

In [236]:
first_key_profile = full_distr(pc_list_distr_first, files.index)
major_corr_first = pd.DataFrame(first_key_profile.groupby(axis = 0, level = 0).profile.apply(lambda x: sp.stats.pearsonr(x, KK(0,0))[0])).rename(columns = {'profile': 'major'})
minor_corr_first = pd.DataFrame(first_key_profile.groupby(axis = 0, level = 0).profile.apply(lambda x: sp.stats.pearsonr(x, KK(1,0))[0])).rename(columns = {'profile': 'minor'})
key_corr_first = pd.concat([major_corr_first, minor_corr_first], axis = 1)


In [237]:
major_dances_first = files.loc[key_corr_first[key_corr_first.minor<=key_corr_first.major].index]
minor_dances_first = files.loc[key_corr_first[key_corr_first.minor>key_corr_first.major].index]

print(f'When looking at the pitch distribution of first phrase only, there are {len(minor_dances_first)} dances whose pitch profile is closer to the minor KK key profile than to the major one.')

When looking at the pitch distribution of first phrase only, there are 68 dances whose pitch profile is closer to the minor KK key profile than to the major one.


In [238]:
detected_minor_first = minor_dances_first[minor_dances_first.index.isin(GT_minor)]
falsely_detected_minor_first = minor_dances_first[~minor_dances_first.index.isin(detected_minor_first.index)]
not_detected_minor_first = major_dances_first[major_dances_first.index.isin(GT_minor)]

print(f'This simple model successfully recognises {len(detected_minor_first)} of the {len(GT_minor)} dances labeled as minor in our ground-truth. It wrongly labels {len(falsely_detected_minor_first)} dances as minor and fails to recognise {len(not_detected_minor_first)} minor dances.')

This simple model successfully recognises 57 of the 63 dances labeled as minor in our ground-truth. It wrongly labels 11 dances as minor and fails to recognise 6 minor dances.


In [239]:
falsely_detected_minor_first.merge(key_corr_first, left_index = True, right_index = True)

D  no      dance                      path gt_mode   entropy  \
29    41  15    menuett   041/D041menuett15a.mscx   major  0.555932   
37    41  19    menuett   041/D041menuett19a.mscx   major  0.599165   
44    91   2    menuett   091/D091menuett02a.mscx   major  0.583645   
51   128   5  deutscher  128/D128deutscher05.mscx   major  0.555251   
125  146  16     walzer     146/D146walzer16.mscx   major  0.567782   
220  420   3  deutscher  420/D420deutscher03.mscx   major  0.570527   
229  420  12  deutscher  420/D420deutscher12.mscx   major  0.607640   
231  421   3  ecossaise  421/D421ecossaise03.mscx   major  0.647691   
299  779   8     walzer     779/D779walzer08.mscx   major  0.581138   
346  783   9  deutscher  783/D783deutscher09.mscx   major  0.560845   
415  972   2  deutscher  972/D972deutscher02.mscx   major  0.523915   

     duration_entropy  onset_entropy     major     minor  
29           1.390226       2.089522  0.509178  0.846547  
37           1.446722       1.944649  0.664435  0.830364  
44           1.356809       1.735498  0.756829  0.830454  
51           1.145856       1.503694  0.703286  0.849986  
125          0.878310       1.564401  0.437819  0.770300  
220          0.861284       1.233569  0.576944  0.584717  
229          1.437751       1.655534  0.680403  0.825352  
231          0.987865       0.837939  0.715494  0.826970  
299          0.943374       1.584548  0.518983  0.688841  
346          0.808492       1.391723  0.092300  0.165038  
415          0.693094       1.611656  0.092300  0.165038

- D041.15 beginning strongly minor
- D041.19 beginning has strong 'minor' feel, but it is just colour.
- D091.2  beginning has strong 'minor' feel, but it is just colour.
- D128.5 progression by thirds over the first phrase (which, however, should include bar 5)
- D146.16 minor start.
- D420.3 first phrase shifts to Bmin.
- D420.12 slightest minor colour in first phrase, within progression by thirds.
- D421.3 long Abmaj chord in bar 4
- D779.8 cadence in Bmin
- D783.9 section 0 is only pick-up measure
- D972.2 section 0 is only pick-up measure


In [240]:
not_detected_minor_first.merge(key_corr_first, left_index = True, right_index = True)

D  no      dance                      path gt_mode   entropy  \
194  366   9    ländler    366/D366ländler09.mscx   minor  0.604576   
245  643   1  deutscher  643/D643deutscher01.mscx   minor  0.672360   
314  779  23     walzer     779/D779walzer23.mscx   minor  0.575870   
342  783   5  deutscher  783/D783deutscher05.mscx   minor  0.540814   
355  783   2  ecossaise  783/D783ecossaise02.mscx   minor  0.555444   
389  924  11     walzer     924/D924walzer11.mscx   minor  0.554017   

     duration_entropy  onset_entropy     major     minor  
194          0.923784       1.417350  0.549020 -0.166303  
245          0.728341       1.690061  0.709750  0.696980  
314          0.819098       1.590646  0.226579  0.219348  
342          0.982174       1.643418  0.661921  0.576631  
355          0.978762       1.007479  0.838473  0.489397  
389          0.781686       1.310137  0.880939  0.642622

- D366.9 I would say this is definitely Bmaj, although it starts in Bmin. The key signature is Bmaj (hence neg. corr with minor).
- D643.1 cadence in Emaj
- D779.23 BEAUTIFUL! is Ebmaj, but starts with II/Gmin, and then moves to Eb through a deceptive cadence.
- D783.5 BEAUTIFUL! is Dmaj but starts with Bmin (just colouring).
- D783.2(ecossaise) starts Bmin (omophonic) but abruptly moves to Dmaj
- D924.11 starts in Emin, but just colouring. No cadence.

Deutscher and Waltzes definitely more likely to exhibit modal shift/colouring in the beginning w.r.t. Landler.

### Clustering keys

### First section

In [241]:
all_corr = files.merge(key_corr_A, left_index = True, right_index = True)
px.scatter(all_corr, x = 'major', y = 'minor', color = 'dance')

In [242]:
all_corr['gt_mode'] = GT_ma_mi

px.scatter(all_corr, x = 'major', y = 'minor', color = 'gt_mode')

In [243]:
files['maj-min'] = all_corr['major'] - all_corr['minor']

### First phrase

In [244]:
all_corr_first = files.merge(key_corr_first, left_index = True, right_index = True)
px.scatter(all_corr_first, x = 'major', y = 'minor', color = 'dance')

Osservation: Based on first phrase, landler are never ambiguous. 

In [245]:
all_corr_first['gt_mode'] = GT_ma_mi

px.scatter(all_corr_first, x = 'major', y = 'minor', color = 'gt_mode')

In [246]:
files['maj-min-first'] = all_corr_first['major'] - all_corr_first['minor']

## event density

In [247]:
measure_list['note_events'] = note_list.groupby(['id', 'mc']).apply(len)
measure_list['note_density'] = measure_list.note_events/measure_list.act_dur.apply(float)
event_density = measure_list.groupby('id').note_density.mean()
event_density.iplot('hist', title = 'Distribution of average event density per bar')

In [248]:
files['event_density'] = event_density
#files.boxplot(column = 'event_density', by = 'dance');
files.set_index('dance', append=True)\
     .event_density\
     .unstack(level=1)\
     .iplot('box')

### Downbeat vs. offbeat densiy

In [249]:
downbeat_density = []
non_downbeat_density = []


for i in range(len(files)):
    if measure_list.loc[i+1,1].act_dur != 3/4:
        downbeat_density += [0]
        non_downbeat_density += [0] 
    else:
        complete_measures_list = list(measure_list[measure_list.act_dur == 3/4].loc[i+1].index.get_level_values('mc'))
        complete_measures = note_list[note_list.mc.isin(complete_measures_list)].loc[i+1]
        downbeats = complete_measures[complete_measures.onset < 1/4]
        non_downbeats = complete_measures[complete_measures.onset >= 1/4]
        downbeat_density += [downbeats.groupby('mn').onset.count().sum()/len(downbeats.mc.unique())]
        non_downbeat_density += [non_downbeats.groupby('mn').onset.count().sum()/(2*len(downbeats.mc.unique()))]
    
files['downbeat_density'] = downbeat_density
files['non_downbeat_density'] = non_downbeat_density

In [250]:
px.scatter(files[files.dance.isin(['menuett', 'trio', 'deutscher', 'walzer', 'ländler'])], x = 'downbeat_density', y = 'non_downbeat_density', color = 'dance', marginal_x = "histogram", marginal_y = "histogram")


### Ratio of downbeat density vs. non-downbeat density, by dance

In [251]:
files['ratio_downbeat_non_downbeat'] = files.downbeat_density/files.non_downbeat_density

In [252]:
files.set_index('dance', append=True)\
     .ratio_downbeat_non_downbeat\
     .unstack(level=1)\
     .iplot('box', yTitle = 'ratio_downbeat_non_downbeat_event_density' )

Osservation: I expected walzes to have a greater downbeat vs. offbeat ratio than other dance types!

#### Onset density

In [253]:
downbeat_onset_density = []
non_downbeat_onset_density = []


for i in range(len(files)):
    if measure_list.loc[i+1,1].act_dur != 3/4:
        downbeat_onset_density += [0]
        non_downbeat_onset_density += [0] 
    else:
        complete_measures_list = list(measure_list[measure_list.act_dur == 3/4].loc[i+1].index.get_level_values('mc'))
        complete_measures = note_list[note_list.mc.isin(complete_measures_list)].loc[i+1]
        
        downbeats = complete_measures[complete_measures.onset < 1/4]
        non_downbeats = complete_measures[complete_measures.onset >= 1/4]
        
        downbeat_onset_density += [downbeats.groupby(['mc', 'onset']).onset.unique().count()/len(downbeats.mc.unique())]
        non_downbeat_onset_density += [non_downbeats.groupby(['mc', 'onset']).onset.unique().count()/(2*len(downbeats.mc.unique()))]
    
files['downbeat_onset_density'] = downbeat_onset_density
files['non_downbeat_onset_density'] = non_downbeat_onset_density

In [254]:
px.scatter(files, x = 'downbeat_onset_density', y = 'non_downbeat_onset_density', color = 'dance')

In [255]:
files['ratio_downbeat_non_downbeat_onset'] = files.downbeat_onset_density/files.non_downbeat_onset_density

In [256]:
files.set_index('dance', append=True)\
     .ratio_downbeat_non_downbeat_onset\
     .unstack(level=1)\
     .iplot('box', yTitle = 'ratio_downbeat_non_downbeat_onset_density')

#### Strictly downbeat/non-downbeat

In [257]:
downbeat_strictly_density = []
non_downbeat_strictly_density = []


for i in range(len(files)):
    
    if measure_list.loc[i+1,1].act_dur != 3/4:
        downbeat_strictly_density += [0]
        non_downbeat_strictly_density += [0] 
    else:
        complete_measures_list = list(measure_list[measure_list.act_dur == 3/4].loc[i+1].index.get_level_values('mc'))
        complete_measures = note_list[note_list.mc.isin(complete_measures_list)].loc[i+1]
        
        onsets = complete_measures.groupby('onset').size()
        
        downbeats = complete_measures.groupby('onset').size().loc[0/4]
        downbeat_strictly_density += [downbeats/len(complete_measures_list)]
        
        non_downbeats = 0
        for k in onsets.index.intersection([1/4, 2/4]):
            non_downbeats += onsets.loc[k]
            
        non_downbeat_strictly_density += [non_downbeats/(2*len(complete_measures_list))]
    
files['downbeat_strictly_density'] = downbeat_strictly_density
files['non_downbeat_strictly_density'] = non_downbeat_strictly_density

In [258]:
px.scatter(files, x = 'downbeat_strictly_density', y = 'non_downbeat_strictly_density', color = 'dance')

In [259]:
files['ratio_downbeat_non_downbeat_strictly'] = files.downbeat_strictly_density/files.non_downbeat_strictly_density

In [260]:
files.set_index('dance', append=True)\
     .ratio_downbeat_non_downbeat_strictly\
     .unstack(level=1)\
     .iplot('box', yTitle = 'ratio_downbeat_non_downbeat_strictly')

## interval statistics for top pseudo-voice

The unfolding of the melodic line represents an highly salient feature of the music, especially in the context of popular dances. In order to stand out from the harmonic texture and be recognisable, the melody is usually formed by the topmost notes played by the right hand of the pianist. The distribution of the intervals separating consecutive notes should reflect typical features such as the prevalence of stepwise motion.

In [261]:
top_pseudovoice = pd.DataFrame(note_list[(note_list.staff == 1) & (note_list.voice == 1)].groupby(['id', 'mc', 'onset']).midi.max())

top_pseudovoice['following_midi'] = top_pseudovoice.groupby('id').midi.shift(-1)

top_pseudovoice = pd.DataFrame(top_pseudovoice.midi - top_pseudovoice.following_midi).apply(abs)

top_pseudovoice.iplot('hist', xTitle = 'midi interval' ,title = 'Distribution of intervals in top-most pseudovoice')

### Interval between first downbeat and first offbeat bass note

In [325]:
measure_list_reindexed = measure_list.set_index(['section'], append = True).swaplevel(1,2)
note_list_reindexed = note_list.set_index(['mc'], append = True).swaplevel(2,3).reset_index(level = 3)

In [362]:
zero_offset_measures = note_list_reindexed.loc[measure_list_reindexed[measure_list_reindexed.offset == 0].index]
interval_downbeat_offbeat = pd.DataFrame(zero_offset_measures[zero_offset_measures.staff == 2].groupby(['id', 'mc', 'onset']).midi.min()).groupby(['id', 'mc']).midi.apply(list).apply(lambda x: x[1]-x[0] if len(x)>1 else 0)
files['interval_downbeat_offbeat'] = interval_downbeat_offbeat.groupby('id').mean()


In [365]:
files.set_index('dance', append=True)\
     .interval_downbeat_offbeat\
     .unstack(level=1)\
     .iplot('box', yTitle = 'interval_downbeat_offbeat')

Landler, walzer and deutscher have registral accent on the downbeat in the bass voice.

### Interval between first downbeat and first offbeat melody note

In [369]:
zero_offset_measures = note_list_reindexed.loc[measure_list_reindexed[measure_list_reindexed.offset == 0].index]
interval_downbeat_offbeat_melody = pd.DataFrame(zero_offset_measures[(zero_offset_measures.staff == 1) & (zero_offset_measures.voice == 1)].groupby(['id', 'mc', 'onset']).midi.max()).groupby(['id', 'mc']).midi.apply(list).apply(lambda x: x[1]-x[0] if len(x)>1 else 0)
files['interval_downbeat_offbeat_melody'] = interval_downbeat_offbeat_melody.groupby('id').mean()

In [371]:
files.set_index('dance', append=True)\
     .interval_downbeat_offbeat_melody\
     .unstack(level=1)\
     .iplot('box', yTitle = 'interval_downbeat_offbeat_melody')

No dance type shows registral accent on the downbeat in the melody.

### Harmonic intervals

In [262]:
def harmonic_intervals(midi_list):
    intervals = []
    for i in range(len(midi_list)):
        for j in range(i, len(midi_list)):
            intervals += [abs(midi_list[j]-midi_list[i])]
    return intervals

vertical_intervals = note_list.groupby(['id', 'mc', 'onset']).midi.apply(list).apply(harmonic_intervals)

In [263]:
sixths = vertical_intervals.apply(lambda x: (8 in x) | (9 in x)).groupby('id').sum()/vertical_intervals.groupby('id').size()                                                               

files['sixths_count'] = sixths


files.set_index('dance', append=True)\
     .sixths_count\
     .unstack(level=1)\
     .iplot('box', yTitle = '#sixths/#onset events')

In [264]:
thirds = vertical_intervals.apply(lambda x: (3 in x) | (4 in x)).groupby('id').sum()/vertical_intervals.groupby('id').size()                                                               

files['thirds_count'] = thirds


files.set_index('dance', append=True)\
     .thirds_count\
     .unstack(level=1)\
     .iplot('box', yTitle = '#thirds/#onset events')

In [265]:
sixths_boolean = pd.DataFrame(vertical_intervals.apply(lambda x: (8 in x) | (9 in x)))

sixths_boolean['following'] = sixths_boolean.groupby('id').shift(-1)

sixths_boolean['both'] = sixths_boolean.midi & sixths_boolean.following

parallel_sixths = sixths_boolean.both.groupby('id').sum()/vertical_intervals.groupby('id').size() 

files['parallel_sixths'] = parallel_sixths

files.set_index('dance', append=True)\
     .parallel_sixths\
     .unstack(level=1)\
     .iplot('box', yTitle = '#parallel_sixths/#onset events')

# Rhythmic patterns

## Full zum-pa-pa

In [266]:
bass_pattern = pd.DataFrame(note_list[note_list.staff == 2].groupby(['id', 'mc']).onset.apply(set))

zumpapa = bass_pattern[bass_pattern.onset == {0, 1/4, 1/2}].groupby('id').size()/measure_list.groupby('id').size()

files['frac_zumpapa'] = zumpapa.fillna(0)

files.set_index('dance', append=True)\
     .frac_zumpapa\
     .unstack(level=1)\
     .iplot('box', yTitle = 'fraction of zumpapa measures')

## Only one-three

In [267]:
one_three = bass_pattern[bass_pattern.onset == {0, 1/2}].groupby('id').size()/measure_list.groupby('id').size()
files['frac_one_three'] = one_three.fillna(0)

files.set_index('dance', append=True)\
     .frac_one_three\
     .unstack(level=1)\
     .iplot('box', yTitle = 'fraction of one-three measures')

## Only one-two

In [268]:
one_two = bass_pattern[bass_pattern.onset == {0, 1/4}].groupby('id').size()/measure_list.groupby('id').size()
files['frac_one_two'] = one_two.fillna(0)

files.set_index('dance', append=True)\
     .frac_one_two\
     .unstack(level=1)\
     .iplot('box', yTitle = 'fraction of one-two measures')

## Duration of downbeat events

In [269]:
downbeat_dur = [] 
for i in range(len(files)):
    
    if measure_list.loc[i+1,1].act_dur != 3/4:
        downbeat_dur += [0]
        
    else:
        complete_measures_list = list(measure_list[measure_list.act_dur == 3/4].loc[i+1].index.get_level_values('mc'))
        complete_measures = note_list[note_list.mc.isin(complete_measures_list)].loc[i+1]
        avg = complete_measures[complete_measures.onset == 0].groupby('mc').duration.apply(list).apply(lambda x: sum(x)/len(x)).mean()
        downbeat_dur += [avg] 

files['downbeat_dur'] = downbeat_dur

In [270]:
files.set_index('dance', append=True)\
     .downbeat_dur\
     .unstack(level=1)\
     .iplot('box', yTitle = 'duration of downbeat')

### distribution by dance type

In [271]:
top_pseudovoice.join(files.dance, on='id')\
               .set_index('dance', append=True)[0]\
               .unstack(level=3)\
               .dropna(how='all').iplot('box')

## Feature Selection For Dance Classification
In the previous sections we have plotted distributions of specific features in the different dancetypes. In this section we want to gather the most discriminative features and investigate if they form meaningful classes

In [272]:
features = files[['dance', 
                  'duration_entropy', 'onset_entropy',
                  'maj-min', 'maj-min-first',
                  'frac_zumpapa',
                  'frac_one_two']]

There are only two instances of the galopp and one of the cotillon so classification cannot be based on training for them. Remove from dataframe of features:

In [273]:
indexNames = features[(features['dance'] == 'galopp') | (features['dance'] == 'cotillon')].index
features.drop(indexNames , inplace=True)

In [274]:
# Add a numerical label in addition to the strings
dance_dict = {'deutscher':0, 'ecossaise':1, 'ländler':2, 'menuett':3, 'trio':4, 'walzer':5}

def label_dance(row):
    return dance_dict[row]

features['dance_num_label'] = features['dance'].apply (lambda row: label_dance(row))

In [275]:
features.head()

dance  duration_entropy  onset_entropy   maj-min  maj-min-first  \
id                                                                      
1   menuett          1.547558       1.693202  0.428511       0.443648   
2      trio          1.186840       2.011860  0.561387       0.633202   
3   menuett          1.415720       1.521429  0.779410       0.620463   
4      trio          0.947097       2.147050  0.576572       0.590081   
5   menuett          1.508821       1.763593  0.342660       0.076347   

    frac_zumpapa  frac_one_two  dance_num_label  
id                                               
1       0.055556      0.555556                3  
2       0.041667      0.083333                4  
3       0.166667      0.111111                3  
4       0.000000      0.090909                4  
5       0.277778      0.111111                3

In [276]:
#nans = lambda df: df[df.isnull().any(axis=1)]
#nans(features)
#features = features.dropna()

In [277]:
from sklearn.manifold import TSNE
import matplotlib.pyplot as plt
from matplotlib import colors

def tSNE(feature_matrix, labels=None, number_of_dances=8):
    if labels is None:
        labels = np.zeros((feature_matrix.shape[0]))

    tsne_features = TSNE(n_components=2).fit_transform(feature_matrix)    
    features['TSNE1'] = tsne_features[:, 0]
    features['TSNE2'] = tsne_features[:, 1]

Scale the features so that they obtain equal importance towards the classifier, regardless of the absolute feature value.

In [278]:
feature_matrix = features[['duration_entropy', 'onset_entropy',
                           'maj-min', 'maj-min-first',
                           'frac_zumpapa', 'frac_one_two']].to_numpy()

labels = features[['dance_num_label']].to_numpy()

In [279]:
from sklearn.preprocessing import StandardScaler

scaler = StandardScaler()
scaler.fit(feature_matrix)
feature_matrix_scaled = scaler.transform(feature_matrix)

In [280]:
tSNE(feature_matrix, labels=labels)

In [281]:
px.scatter(features, x = 'TSNE1', y = 'TSNE2', color = 'dance')

## Training An SVM classifier On The Features

In [282]:
from sklearn import svm
from sklearn.metrics import confusion_matrix
from sklearn.model_selection import train_test_split

Split the data into training and test set

In [283]:
labels = np.ravel(labels)
features_train, features_test, labels_train, labels_test = train_test_split(feature_matrix_scaled,
                                                                            labels,
                                                                            test_size=0.33,
                                                                            random_state=43)

Train a classifier and predict labels for the test set

In [284]:
clf = svm.SVC(gamma='scale', C=100, decision_function_shape='ovr')
clf.fit(features_train, labels_train)

SVC(C=100, cache_size=200, class_weight=None, coef0=0.0,
    decision_function_shape='ovr', degree=3, gamma='scale', kernel='rbf',
    max_iter=-1, probability=False, random_state=None, shrinking=True,
    tol=0.001, verbose=False)

In [285]:
labels_predicted = clf.predict(features_test)

Assess the result by computing a confusion map

In [286]:
cm = confusion_matrix(labels_test, labels_predicted)
cm = cm.astype('float') / cm.sum(axis=1)[:, np.newaxis] # Normalize confusion map
cm = np.around(cm, decimals=2)
#print(cm)

In [287]:
import plotly.graph_objects as go
dance_list = list(dance_dict.keys())

import plotly.figure_factory as ff
fig = ff.create_annotated_heatmap(z=cm, x=dance_list, y=dance_list)

#fig = go.Figure(data=go.Heatmap(z=cm, x=dance_list, y=dance_list))
fig.update_layout(title='Confusion Map For Dance Classification',
                  xaxis_title="Predicted labels", yaxis_title="True labels")
fig.data[0].update(zmin=0, zmax=1)
fig.show()

## Beyond Ländler & Co.: Can we extract musically meaningful clusters from features?

In this section, try to find meaningful clusters in our feature space using K-means and analyse what these dances might have in common.

In [288]:
from sklearn.cluster import KMeans

In [289]:
kmeans = KMeans(n_clusters=4).fit(features[['duration_entropy', 'onset_entropy',
                                            'maj-min', 'maj-min-first',
                                            'frac_zumpapa', 'frac_one_two']])
centroids = kmeans.cluster_centers_

In [290]:
features['kmeans_label'] = kmeans.labels_.astype(float)

In [291]:
px.scatter(features, x = 'TSNE1', y = 'TSNE2', color = 'kmeans_label')
px.scatter(centroids[:, 0], centroids[:, 1], c='red', s=50)

TypeError: scatter() got an unexpected keyword argument 'c'

Sample some dances from the middle of the clusters to listen to them:

In [ ]:
sampleClass0 = features.loc[(features['TSNE1'] >= 12) & (features['TSNE1'] <= 14) &
                            (features['TSNE2'] >= 12) & (features['TSNE2'] <= 14)]
class0Examples = files.iloc[sampleClass0.index]

sampleClass1 = features.loc[(features['TSNE1'] >= -15) & (features['TSNE1'] <= -12) &
                            (features['TSNE2'] >= 8) & (features['TSNE2'] <= 10)]
class1Examples = files.iloc[sampleClass1.index]

sampleClass2 = features.loc[(features['TSNE1'] >= 15) & (features['TSNE1'] <= 17) &
                            (features['TSNE2'] >= -22) & (features['TSNE2'] <= -20)]
class2Examples = files.iloc[sampleClass2.index]

sampleClass3 = features.loc[(features['TSNE1'] >= 0) & (features['TSNE1'] <= 5) &
                            (features['TSNE2'] >= -3) & (features['TSNE2'] <= -1)]
class3Examples = files.iloc[sampleClass3.index]

Listening to some of these pieces does not really indicate any relevant similarities within classes. Maybe try again with different features at a later point?

# roadmap for the project



## repeating pattern detection with autocorrelation

Responsible: Sébastien

Plan: Autocorrelation within every piece

* from the smallest window size to the biggest
* show results as triangular *f-scape* plot
* try different representations (rhythmical, pitch-related, textural) of every window and different distance measures

From this exploration, see which are the most promising results for further in-depth analysis.

Hypotheses:
* autocorrelation of rhythms (=very abstract representation), we expect accurate detection of repeated patterns of any length (e.g. of length 1 or 2 measures, or 8-measure-sections)
    * this will allow for formal analysis, i.e. deciding when a piece has form AABB, ABA etc.
    * it will give us reasonable segmentations of every piece by seeing, which rhythmic patterns repeat several times
* departing from the detected segmentations we can expect that the same rhythmic patterns are repeated using differnt pitches; autocorrelation might be a way to compute the harmonic and diastematic relationships

In [ ]:
def notes_xcor(product, notes_a, notes_b, name=None):
    """ Compute the (cross-)correlation of one dataframe of notes over another one.
    Args:
        product Product function, mapping two measures of notes to a summable value
        notes_a First non-empty dataframe of notes (usually the smallest)
        notes_b Second non-empty dataframe of notes (can be the same)
        name    Given name for this cross-correlation
    Returns:
        Correlation dataframe
    """ 
    # Production computation helper
    def compute(ma, mb):
        return product(notes_a[notes_a["mc"] == ma], notes_b[notes_b["mc"] == mb])
    # Get the range of offsets
    alength = notes_a["mc"].max() + 1
    blength = notes_b["mc"].max() + 1
    mlength = min(alength, blength)
    offsets = list(range(1 - alength, blength))
    # Compute the correlation
    results = list()
    for offset in offsets:
        results.append(sum(compute(x, x + offset) for x in range(0, mlength)))
    # Transform into a dataframe
    return pd.DataFrame(results, index=offsets, columns=["xcor" if name is None else "xcor-%s" % name])

In [ ]:
def product_rhythm(meas_a, meas_b):
    """ Count for how many times notes starts at the same onset.
    Args:
        meas_a Measure A
        meas_b Measure B
    Returns:
        How many times at least two notes from the two measures start at the same time 
    """
    sa = set(meas_a["onset"])
    sb = set(meas_b["onset"])
    return len(sa.intersection(sb))

In [ ]:
notes_a = note_list.loc[1]
notes_b = note_list.loc[1]
for i in range(1, 8):
    xcor = notes_xcor(product_rhythm, notes_a[notes_a["mc"] < i], notes_b)
    xcor /= xcor["xcor"].max()
    xcor.plot()

## harmony inference and detection of musical schemata

Responsible: Johannes H.

This part will be using results from Johannes H's PhD project to come up with an automatic segmentation and labelling of harmonies. The point of departure is a distribution of notes  for every possible chord label, as it was avaraged over the occurrence of this chord label in several different corpora. Using an automated analysis approach with incremental windows, the windows' note distribution will be matched to the most likely label using Bayesian statistics. A short literature research should reveal existing matching algorithms, otherwise one has to be developed.

## supervised classification of dance types

Responsible: Gabriele, Johannes R.

The different types of Schubert dances have been composed for different purposes, target audiences, dances and contexts. This is reflected in their perceived musical character. In this part of the project we want to extract features from the score data that indicate these changes. This requires fusioning data analysis and musicological background information. The classification therefore mainly consists of two parts:
1. Scan of musicological literature for existing hypothesis that might hint at structural differences in the composition.
2. Supervised classification based on basic statistics, outcomes of the other project's strands and features computed from pattern detection and other metrics derived from the musicological and historical context. These include: 

    - time and key signature
    - key-similarity profiles (see above) 
    - melodic and harmonic interval distributions (see above)
    - event density distribution (see above)
    - recurring patterns.

The exact classification method will be dependent on the amount of features that we gather. A random forest model, ranking the features by their relevance, might help us to identify the most important criteria. Due to the sheer amount of dances, it is difficult for a human without extensive training to oversee the relevant differences. With this larger scale analysis we hope to extract some of the distinguishing factors.

It is also plausible that no notation-related feature among those commonly associated to individual dance types happens to be a strong predictor of dance type, and this would also be an interesting result: the character of the dance might then be hypothesised to correspond to the character of a performer's rendition, rather than to the written-out skeleton of the music. 

The project strands will be developed in parallel until the first scheduled meeting, and the outcomes are expected to be muually relevant already from the early stages.  

# Internal: How plotting works

As you have seen, it is enough to put `.iplot()` behind your dataframe to plot it. First argument is `kind=`.

In [ ]:
transposed_distribution[['count_n', 'duration_n']]\
                       .iplot('bar', xTitle='Tonal Pitch Class', yTitle='Normalized note counts & durations')

(This is the only page you need for Cufflinks documentation including examples: https://plot.ly/python/v3/ipython-notebooks/cufflinks/)

If you want to store the file to disk in a format of your choice, you can use the wrapper function `plot`, where `args` are the arguments used for `.iplot()` above:

    plot(df, filename, args)
So, in order to create the same plot as above while storing it as `test.pdf`, you can do:

    plot(transposed_distribution[['count_n', 'duration_n']], 'test.pdf', 'bar', xTitle='Tonal Pitch Class', yTitle='Normalized note counts & durations')

Or, if you want to have the same code in a more readable form:

    df = transposed_distribution[['count_n', 'duration_n']]
    kwargs = {'kind': 'bar', 
              'xTitle': 'Tonal Pitch Class', 
              'yTitle':'Normalized note counts & durations'}
    plot(df, 'test.pdf', **kwargs)